In [164]:
import pandas as pd
import glob
import json
import numpy as np 
import re
import nltk
from sklearn.feature_extraction.text import TfidfVectorizer,CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.cluster import KMeans
from nltk.tokenize import sent_tokenize, word_tokenize
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\gila0000\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\gila0000\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\gila0000\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [165]:
# random functions
def get_random():
    files = glob.glob(r'CORD-19-research-challenge/**/pdf_json/*.json', recursive=True)
    random_files = np.random.choice(files, int(len(files)*.1))
    return random_files

In [166]:
# Write a file reader a file and tokenize the data.

def reader ():
    File = get_random()
    dataframe = {"title": [],"text_abstract":[], "text_body": []}
    dataframe = pd.DataFrame.from_dict(dataframe)
    for i,file in enumerate (File):
        tuples = {"title": None, "text_abstract": None,"text_body": None}
        with open(file) as json_data:
            
            data = json.load(json_data)
        
            tuples['title']=data['metadata']['title']
               
            abstract_text= []
            body_text = []
        
            for a in data['abstract']:
                abstract_text.append(a['text'])
                
       
            for b in data['body_text']:
                body_text.append(b['text'])
            

            body = "\n ".join(body_text)
            abstract = "\n". join(abstract_text)
            tuples["text_abstract"] = abstract
            tuples['text_body']=body 
            dataframe = dataframe.append(tuples, ignore_index=True)

    return dataframe

In [167]:
df = reader()

In [168]:
stop_words = nltk.corpus.stopwords.words('english')
stop_words
stop_words[:20]
len(stop_words)

179

In [174]:
def normalize(txt):
    #txt = reader()
    txt = re.sub(r'[^a-zA-Z0-9\s]', ' ', str(txt), re.I|re.A)
    txt = re.sub("(^|\W)\d+($|\W)", " ", txt)   #remove whitespace and numbers
    txt = txt.replace('title', '')       #remove 'title'
    txt = re.sub('[!#?%*&$)@^(.,-=+:";]', '', txt)       #remove punctuation
    txt = re.sub(r"\b[a-zA-Z]\b",'',txt)        #remove single letters
    txt = re.sub(r'\d+', '', txt)
    txt = re.sub(r'\\b[A-Z a-z 0-9._ - ]*[@](.*?)[.]{1,3} \\b', '', txt)#remove email
    txt = txt.replace('introduction', '')       #remove 'introduction'
    txt = txt.replace('text', '')
    txt = txt.replace('background', '')         #remove 'background'
    txt = txt.replace('abstract', '') 
    txt = txt.replace('\\n', ' ')   
    txt = txt.replace('\n', ' ')
    txt = txt.replace('///', ' ') 
    txt = txt.replace("'", '')
    txt = re.sub(r'^\w\w?$', '',txt) 
    txt = txt.lower()
    return txt

In [175]:
from nltk.stem import WordNetLemmatizer
def wordtokenizing(txt):
    wordnet_lemmatizer = WordNetLemmatizer()
    word = normalize(txt)
    tokens = nltk.word_tokenize(word)
    word_tokens = [t for t in tokens if t not in stop_words]
    lemmatized_word = [wordnet_lemmatizer.lemmatize(word) for word in word_tokens]
    return ' '.join(word_tokens)


In [176]:
normalize_corpus = np.vectorize(wordtokenizing, otypes=[np.ndarray])

In [177]:
norm_corpus = normalize_corpus(list(df['text_body']))

In [178]:
tf = TfidfVectorizer(preprocessor= wordtokenizing,stop_words=stop_words)
tfidf_matrix = tf.fit_transform(norm_corpus)
tfidf_matrix .shape

(4594, 263345)

In [ ]:
from sklearn import metrics
from scipy.spatial.distance import cdist
import matplotlib.pyplot as plt

# run kmeans with many different k
distortions = []
K = range(1, 50)
for k in K:
    km = KMeans(n_clusters=k, random_state=42).fit(r)
    km.fit(r)
    distortions.append(sum(np.min(cdist(X_reduced, k_means.cluster_centers_, 'euclidean'), axis=1)) / tfidf_matrix.shape[0])


X_line = [K[0], K[-1]]
Y_line = [distortions[0], distortions[-1]]

# Plot the elbow
plt.plot(K, distortions, 'b-')
plt.plot(X_line, Y_line, 'r')
plt.xlabel('Number of cluster')
plt.ylabel('Distortion')
plt.title('The Elbow Method showing the optimal k')
plt.show() 

In [197]:
from sklearn.cluster import KMeans
km = KMeans(n_clusters=10,init='k-means++')
km.fit(tfidf_matrix)

KMeans(algorithm='auto', copy_x=True, init='k-means++', max_iter=300,
       n_clusters=10, n_init=10, n_jobs=None, precompute_distances='auto',
       random_state=None, tol=0.0001, verbose=0)

In [180]:
%time
%timeit
df['kmeans_cluster'] = km.labels_

Wall time: 0 ns


In [232]:
from sklearn.metrics import silhouette_score
score_max = -1 #this is the minimum possible score
for k in range(1,10):
    silhout= silhouette_score(tfidf_matrix,  df['kmeans_cluster'])
    print ("For n_clusters = {}, silhouette score is {})".format(k,silhout))

For n_clusters = 1, silhouette score is 0.016029273587150627)
For n_clusters = 2, silhouette score is 0.016029273587150627)
For n_clusters = 3, silhouette score is 0.016029273587150627)
For n_clusters = 4, silhouette score is 0.016029273587150627)
For n_clusters = 5, silhouette score is 0.016029273587150627)
For n_clusters = 6, silhouette score is 0.016029273587150627)
For n_clusters = 7, silhouette score is 0.016029273587150627)
For n_clusters = 8, silhouette score is 0.016029273587150627)
For n_clusters = 9, silhouette score is 0.016029273587150627)


In [252]:
text_clusters = (df[['kmeans_cluster', 'text_body']]
                  .sort_values(by=['kmeans_cluster', 'text_body'], 
                               ascending=False)
                  .groupby('kmeans_cluster').head(20))

In [257]:
topn_features = 9
ordered_centroids = km.cluster_centers_.argsort()[:, ::-1]
ordered_centroids

array([[ 35975, 252151, 141888, ..., 151979, 151978,      0],
       [ 37783,  37609, 146025, ..., 164159, 164158,      0],
       [174775,  50635, 183608, ..., 168811, 168810,      0],
       ...,
       [101310, 193394,  34876, ..., 166309, 166308,      0],
       [144409,  50562, 144415, ..., 173157, 173156,      0],
       [191341, 252151, 205598, ..., 162336, 162335, 131672]], dtype=int64)

In [258]:
feature_names = tf.get_feature_names()

In [259]:
for cluster_num in range(10):
    key_features = [feature_names[index] 
                        for index in ordered_centroids[cluster_num, :topn_features]]
    texts =text_clusters[text_clusters['kmeans_cluster'] == cluster_num]['text_body'].values.tolist()
    print('CLUSTER #'+str(cluster_num+1))
    print('-'*20)
    print('Key Features:', key_features)
    print('Text :', texts)
    print('-'*80)

IndexError: list index out of range

In [ ]:
import networkx as nx
from sklearn.metrics.pairwise import cosine_similarity
for cluster_num in range(0,10):
    texts =text_clusters[text_clusters['kmeans_cluster'] == cluster_num]['text_body'].values.tolist()
    print('CLUSTER #'+str(cluster_num+1))
    print('-'*80)
    
       
    text_summary = wordtokenizing(texts)

    tf = TfidfVectorizer()
    text_summary  = [text_summary ]
    tf_mat = tf.fit_transform(text_summary)

    matrix = (tf_mat*tf_mat.T)
    nx_form =nx.from_scipy_sparse_matrix(matrix)

    ranks =nx.pagerank(nx_form)

    similairity = np.zeros([len(text_summary), len(text_summary)])
    from sklearn.metrics.pairwise import cosine_similarity
    cosin = cosine_similarity(fitting[0:1], fitting)
    trans = cosin  * cosin .T

    nx_graph = nx.from_numpy_array(trans)
    s = nx.pagerank(nx_graph)
    ranked_sentences = sorted(((s[i],n) for i,n in enumerate(text_summary)), reverse=True)
    print("Indexes of top ranked_sentence order are ", ranked_sentences)




In [ ]:
for i in range( len(texts)):
    print(ranked_sentences[i][1])
   

In [231]:
for cluster_num in range(0,10):
    print('CLUSTER #'+str(cluster_num+1))
    print('-'*80)
    text_summary.append(" ".join(ranked_sentences[cluster_num][1]))

    # output the summarize texr
    print("Summarize Text: \n", ". ".join(text_summary))

CLUSTER #1
--------------------------------------------------------------------------------
Summarize Text: 
 ufb chiropractic entities sample recognized covid crisis emerging moved quickly responses ufb established safe working environment entity staff services chiropractic profession could continue ufb delivered communications stakeholders guide decisions direct actions stakeholders could make best decisions possible situation ufb continuing monitor situation respond new information becomes available deadly disease infected millions taken thousands lives numbers continue climb world health organization developed multiple measures respond pandemic including providing resources recommendations action pandemic created unique challenges practice education health professionals around world chiropractors patients public serve facing unknown territory navigate health care public health response according world federation chiropractic nearly chiropractors world majority chiropractic healthca

IndexError: list index out of range

In [219]:
for cluster_num in range(0,10):
    key_features = [feature_names[index] 
                        for index in ordered_centroids[cluster_num, :topn_features]]
    texts =text_clusters[text_clusters['kmeans_cluster'] == cluster_num]['text_body'].values.tolist()
    print('CLUSTER #'+str(cluster_num+1))
 
    print('-'*80)
    nlp = en_core_web_sm.load()

# add PyTextRank to the spaCy pipeline
    tr = pytextrank.TextRank()
    nlp.add_pipe(tr.PipelineComponent, name="textrank", last=True)

    doc = nlp(str(texts))
        
     
    for token in doc._.phrases:
        print(token.text, '|', token.rank)

   

CLUSTER #1
--------------------------------------------------------------------------------
sars infection | 0.06696761625398835
sars patients | 0.06695687963014531
sars cases | 0.06570966553878833
sars | 0.06419141548548374
acute sars infections | 0.06312412696317964
acute sars patients | 0.06311440722591405
adult sars patients | 0.06305159318433111
pediatric sars patients | 0.06304142903615192
sars transmission | 0.06277620664328966
probable sars patients | 0.062441194992379316
new sars cases | 0.062364973247293114
recovering sars patients | 0.06236222377135184
cumulative sars cases | 0.06177574479923795
severe sars disease | 0.06144655495180787
sars outbreaks | 0.06111526627320037
sars specimens | 0.060867130569732884
sars accumulative cases | 0.06079878037008257
sars severity | 0.060792221777831806
acute sars | 0.060510827239188575
pediatric sars | 0.06042161202762328
sars coronavirus | 0.06021711261085862
sars vaccine development | 0.06006946515436451
sars disease enhancement | 0.

permissive cell-lines | 0.021104597928064135
the specific virus | 0.021094757574577756
mers-cov. | 0.021092783525554635
large numbers | 0.02109177293119916
healthy controls | 0.02107986503067409
day | 0.02106109287773683
human and veterinary vaccines | 0.021032982522542525
chimeric mers vlps | 0.020978485140801122
crystallographic data collection | 0.020966068701439328
a comprehensive gene expression profile | 0.02094432589819889
an infectious tuberculosis patient | 0.020934077622417543
efficient human-tohuman transmission | 0.02093364312335901
macrophage or epithelial cell origin | 0.020933313538684266
mers-s | 0.02093285502561501
rna | 0.0209270716045271
smaller number | 0.020925920590369657
humanto-human transmission capacity | 0.020924134066622066
respiratory failure | 0.02091994824767677
respiratory route | 0.02091573274811982
specific technology platforms | 0.02090795192466476
spot-forming cells | 0.020887902625196415
the mers-cov cellular receptor | 0.02085290415448317
dpp4 | 0.

personal protective equipment.\n data | 0.014120214962916829
level | 0.014102703314849425
slaughterhouse personnel | 0.01409125026378925
neither the infection status | 0.014081874701970242
the x-ray crystal structure | 0.01407863928935609
the high press coverage | 0.014075699539348174
strains | 0.014064502720965712
hand gloves | 0.014058660453529298
the highest peak | 0.014047941706550621
the available data | 0.014047511609930648
s1 domain | 0.014046280017794073
the hong kong outbreak | 0.014042680967524155
a lower reproduction number | 0.01402068651230366
recombinant baculovirus m1-st | 0.014017323691567902
a significant respiratory impairment | 0.014015616142800348
chronic renal failure | 0.014002919613932914
an attractive model | 0.014002376304141447
an alternative model | 0.014001489499548977
a valid model | 0.013999936686116276
polytron pt2100 tissue grinders | 0.013997760638628405
laboratory investigation | 0.013991211429288924
family and hospital outbreaks | 0.013987609253090009

ifn-β | 0.009399564256493501
the same gap procedure | 0.009397109465904434
the interaction patterns | 0.009395906307624734
the present strategy | 0.009387449036422918
physical examination | 0.00938431510785054
asn229gln mutant | 0.009383989196266661
healthy women | 0.009382750428713876
surface plasmon resonance | 0.009379604789576064
the gap-derived severity | 0.00937727689278852
the prolonged suspension period | 0.009375374257017757
seat assignment proximity | 0.009371416180925362
intranasal inoculation | 0.0093645986741111
the low-titer baculoviruses | 0.009354129656368749
the tested length | 0.009335091245788726
droplets | 0.00932731015217909
combinational ribavirin | 0.00932583563513003
key components | 0.009320614029159364
grand island | 0.009318433244630681
proprietary adjuvants | 0.009314649339637588
sore throat | 0.009314566436421317
peptides | 0.00930753419794678
the envelop spike | 0.009306961026605233
the first meeting | 0.009306406960524214
6 following transfection | 0.0093

as37 | 0.0065737512054573136
embase | 0.006568599591888696
the total cu-\n dn | 0.006555951886079203
immunostaining techniques | 0.00655406320954307
an spike s1 | 0.006552998174704704
the crystallographic software | 0.006551030232504143
immunohistochemistry | 0.00654536647804523
endotracheal intubations.\n | 0.006529830471143335
the common marmoset | 0.006522420373806136
hdpp4 | 0.006522267587343614
the baculovirus platform | 0.006516859238722278
c407 | 0.006511254843564785
subpleural consolidation | 0.006510748865931733
the log ratios | 0.006508277049909015
the causative agent | 0.006505243368286288
this novel pathogen | 0.006501679397359893
a "global threat | 0.0064968345733297135
stomach | 0.006496315306281493
monocyte-tropic chemokines | 0.006494909388366311
the heptad repeat 2 region | 0.006494382261715711
the cellular exudates | 0.0064936458881447254
a relatively flat surface | 0.006491802793722901
ad5-hdpp4 transduction | 0.006491480324624357
gastrointestinal bleeding | 0.006487

...

fetal complications | 0.005889717783929759
org/pets/pet_care/dog_care/stay_dog_bite_free/index | 0.005889070820009857
avian | 0.005888750880471792
no recent stay | 0.00588814182625301
an integral part | 0.005885960290630748
a particular subfield | 0.005882487661774939
mapping | 0.00587893334914202
the global outbreak alert and response network | 0.005878871774647283
geneva | 0.005875060237765222
gene transfer | 0.005872303688250426
frustration | 0.005872245224687798
sporothrix | 0.005872245224687798
hairdo | 0.005872245224687798
a university\s host region | 0.005870754228766777
the cultural geographer | 0.005869093391430352
χ 2 tests.\n a multivariate logistic regression model | 0.00586739183203386
the significantly lower mortality | 0.005867235925688203
the diverse networks | 0.005864791222842132
macroeconomic stability | 0.0058635676101353095
consultation | 0.005861604727169503
a confidential internal document | 0.005860257401352509
those products | 0.005859818472741615
the relative 

the executive directors | 0.0047202387039904925
polymicrobial flora | 0.004719349370156516
fig | 0.004717146559295705
railway tracks | 0.004712450276363544
nd | 0.004711826619140027
allergy | 0.004710812340294869
the normative framework | 0.004710252905909125
an airborne route | 0.004709455457954301
• humane society | 0.004708770819130505
chapter | 0.004707460533327452
a daily basis | 0.004703633802778376
utilitarian | 0.004702609565373486
cocoa | 0.004698817570856504
the sierra leone\ | 0.004698372530131411
the latest updates | 0.004698129800414288
a qualitative description | 0.004694838157342291
variations | 0.0046935325569779605
the third millennium | 0.004689654596393008
lcmv | 0.004689002450015905
whistle | 0.004688254430492046
excellence | 0.004687828076913356
november | 0.004683468121792767
contraction | 0.004682865373188903
who\s mandate | 0.004681722218169803
the tainted syringes | 0.004680408856097851
chances | 0.00467954345275054
a superficial and unsatisfying discussion | 0

streptococcus | 0.0036079776834417408
hamsters | 0.003607727973529557
territorial | 0.0036072462287528705
fraser | 0.003607028176008774
lebanese | 0.0036061351825099983
its functions | 0.0036057950708197335
(b-cell lines | 0.003602565948594705
an additional $170 million package | 0.003601447961354594
(t = −2.3 | 0.0036006198599262155
the extreme partisanship | 0.003596883631381812
versus | 0.0035963122509777602
cauchemez | 0.0035944347549131984
inciardi | 0.0035944347549131984
caregivers | 0.0035924576898229777
hawaii | 0.003592123788992689
accordance | 0.003591865129181049
its 2011 report-"the world | 0.0035888875311918156
wife | 0.003587576953202835
electrolytes | 0.003587130380555278
civets | 0.003584272962349455
more extensive information.\n | 0.0035809652795141815
concepts.\n | 0.0035800161545042775
discharge | 0.0035788556500785003
lagos | 0.003578197114613156
this.\n | 0.003576623795344008
appropriateness | 0.0035763383754565726
georgia | 0.0035754528973206768
the following webs

avma | 0.0022743107960063675
exposure.\n | 0.0022743107960063675
http://www.hsus | 0.0022743107960063675
htm | 0.0022743107960063675
http://www.cdc.gov/ncipc/duip/biteprevention.htm.\n | 0.0022743107960063675
regularly.\n | 0.0022743107960063675
reasons.\n | 0.0022743107960063675
organizations.\n | 0.0022743107960063675
difference?\n | 0.0022743107960063675
queue.\n | 0.0022743107960063675
bounds | 0.0022743107960063675
utility.\n | 0.0022743107960063675
it.\n | 0.0022743107960063675
how?\n | 0.0022743107960063675
despair | 0.0022743107960063675
speed | 0.0022743107960063675
numbers.\n | 0.0022743107960063675
weather.gov/crp/hurricane_harvey | 0.0022743107960063675
nigeria | 0.0022743107960063675
"\n | 0.0022743107960063675
year.\n | 0.0022743107960063675
threat:\n | 0.0022743107960063675
jacob | 0.0022743107960063675
ppe.html | 0.0022743107960063675
p=0.60 | 0.0022743107960063675
paid.\n | 0.0022743107960063675
the marketing | 0.0022729005137936266
the delivery | 0.002272209538067275


ValueError: [E088] Text of length 1721497 exceeds maximum of 1000000. The v2.x parser and NER models require roughly 1GB of temporary memory per 100,000 characters in the input. This means long texts may cause memory allocation errors. If you're not using the parser or NER, it's probably safe to increase the `nlp.max_length` limit. The limit is in number of characters, so you can check whether your inputs are too long by checking `len(text)`.

In [225]:
for cluster_num in range(0,10):
    key_features = [feature_names[index] 
                        for index in ordered_centroids[cluster_num, :topn_features]]
    texts =text_clusters[text_clusters['kmeans_cluster'] == cluster_num]['text_body'].values.tolist()
    print('CLUSTER #'+str(cluster_num+1))
 
    print('-'*80)
    nlp = en_core_web_sm.load()

# add PyTextRank to the spaCy pipeline
    tr = pytextrank.TextRank()
    nlp.add_pipe(tr.PipelineComponent, name="textrank", last=True)

    doc = nlp(str(texts))

    for sent in doc._.textrank.summary(limit_phrases=20, limit_sentences=5):
        print(sent)



CLUSTER #1
--------------------------------------------------------------------------------
To determine an association between seating proximity to the SARS patient and transmission of SARS, a study that included all airline passengers seated within four rows (i.e., front, back, and same row) of the index patient (4) was conducted.
IgG. The rest of 33 RNA specimens from SARS patients were labelled as recovering SARS (RS).
The only two unexplained specimens, RS18 and RS71 from the same patient, may represent a unique biological variability, accounting for the misclassification using this 52-gene molecular signature.\n To test the efficacy of using these 52 genes as the molecular signature for the severity of SARS patients, we identified a significant correlation (P < 1 × 10 -6 ) between the derived rank of SARS severity and the number of days after the onset of disease (Fig. 4a) .
The increase rate of SARS cases is expected to decrease with the cumulative SARS cases, which corresponds 

ValueError: [E088] Text of length 1721497 exceeds maximum of 1000000. The v2.x parser and NER models require roughly 1GB of temporary memory per 100,000 characters in the input. This means long texts may cause memory allocation errors. If you're not using the parser or NER, it's probably safe to increase the `nlp.max_length` limit. The limit is in number of characters, so you can check whether your inputs are too long by checking `len(text)`.

In [76]:
str1 = ''.join(texts)